# 🚀 Ollama sur Google Colab (GPU Gratuit)

Ce notebook configure Ollama avec GPU Tesla T4 gratuit sur Google Colab.

## ⚡ Configuration rapide

1. **Activer le GPU** : Runtime → Change runtime type → T4 GPU
2. **Exécuter les cellules** dans l'ordre

In [ ]:
# 1. Vérifier le GPU
!nvidia-smi
import torch
print(f"GPU disponible: {torch.cuda.is_available()}")
print(f"GPU: {torch.cuda.get_device_name(0) if torch.cuda.is_available() else 'Aucun'}")

In [ ]:
# 2. Installer Ollama
!curl -fsSL https://ollama.com/install.sh | sh

In [ ]:
# 3. Démarrer Ollama en arrière-plan
import subprocess
import time

# Démarrer le serveur
process = subprocess.Popen(['ollama', 'serve'], stdout=subprocess.PIPE, stderr=subprocess.PIPE)
time.sleep(5)
print("✅ Serveur Ollama démarré")

In [ ]:
# 4. Télécharger des modèles
print("📥 Téléchargement des modèles...")

# Modèles recommandés pour T4 16GB
models = [
    "llama3.2:3b",      # 3B params, rapide
    "phi3:medium",      # 14B params, Microsoft
    "mistral:7b-instruct", # 7B params, très bon
    "deepseek-r1:7b"    # 7B params, raisonnement
]

for model in models:
    print(f"\n📦 Téléchargement {model}...")
    !ollama pull {model}
    print(f"✅ {model} prêt")

In [ ]:
# 5. Interface de chat simple
import json
import requests

def chat_ollama(prompt, model="llama3.2:3b"):
    """Chat avec Ollama"""
    response = requests.post(
        "http://localhost:11434/api/generate",
        json={
            "model": model,
            "prompt": prompt,
            "stream": False
        }
    )
    return response.json()['response']

# Test
print("🤖 Test avec llama3.2:3b")
print("-" * 50)
response = chat_ollama("Quelle est la capitale de la France ? Réponds en une phrase.")
print(response)

In [ ]:
# 6. Interface interactive
from IPython.display import display, HTML, clear_output
import ipywidgets as widgets

# Widgets
model_dropdown = widgets.Dropdown(
    options=['llama3.2:3b', 'phi3:medium', 'mistral:7b-instruct', 'deepseek-r1:7b'],
    value='llama3.2:3b',
    description='Modèle:'
)

prompt_text = widgets.Textarea(
    value='',
    placeholder='Tapez votre question ici...',
    description='Question:',
    layout=widgets.Layout(width='100%', height='100px')
)

output_area = widgets.Output()
button = widgets.Button(description="Envoyer", button_style='primary')

def on_button_click(b):
    with output_area:
        clear_output()
        print(f"🤖 {model_dropdown.value} répond...")
        print("-" * 50)
        response = chat_ollama(prompt_text.value, model_dropdown.value)
        print(response)
        prompt_text.value = ""

button.on_click(on_button_click)

# Afficher l'interface
display(HTML("<h3>💬 Chat avec Ollama sur GPU</h3>"))
display(model_dropdown)
display(prompt_text)
display(button)
display(output_area)

In [ ]:
# 7. Test de performance
import time

print("⚡ Test de performance GPU vs CPU")
print("=" * 50)

test_prompt = "Écris un haïku sur l'intelligence artificielle."

for model in ['llama3.2:3b', 'mistral:7b-instruct']:
    print(f"\n📊 Test {model}")
    start = time.time()
    response = chat_ollama(test_prompt, model)
    elapsed = time.time() - start
    
    print(f"Temps: {elapsed:.2f} secondes")
    print(f"Réponse: {response[:100]}...")
    print(f"Vitesse: ~{len(response.split())/elapsed:.1f} mots/seconde")

In [ ]:
# 8. Connexion avec Open WebUI (optionnel)
print("🌐 Configuration pour Open WebUI externe")
print("=" * 50)

# Installer ngrok pour exposer Ollama
!pip install pyngrok -q

from pyngrok import ngrok

# Créer un tunnel
tunnel = ngrok.connect(11434)
print(f"\n✅ Ollama accessible à: {tunnel.public_url}")
print(f"\n📝 Configuration Open WebUI:")
print(f"   - URL Ollama: {tunnel.public_url}")
print(f"   - Modèles disponibles: {', '.join(models)}")
print(f"\n⚠️  Note: Le tunnel expire après 2 heures")

## 📚 Guide d'utilisation

### 🎯 Modèles recommandés par usage

| Modèle | Taille | Usage | Vitesse T4 |
|--------|--------|-------|------------|
| llama3.2:3b | 3B | Chat rapide | ~50 tokens/s |
| mistral:7b | 7B | Polyvalent | ~30 tokens/s |
| phi3:medium | 14B | Raisonnement | ~15 tokens/s |
| deepseek-r1:7b | 7B | Analyse | ~25 tokens/s |

### ⏱️ Limites Colab gratuit
- Session max : 12 heures
- GPU : Tesla T4 16GB
- Inactivité : Déconnexion après 90 min

### 💡 Astuces
1. Sauvegardez régulièrement votre travail
2. Utilisez `llama3.2:3b` pour les réponses rapides
3. Passez à `mistral:7b` pour plus de qualité
4. Le tunnel ngrok permet d'utiliser Open WebUI depuis votre navigateur